# Set-up

## Install packages

In [1]:
!pip install geopandas
import geopandas as gpd

!pip install geojson
import geojson

from shapely.geometry import Point
import folium
import matplotlib, matplotlib.pyplot as plt 
import numpy as np 

You should consider upgrading via the '/home/ubuntu/.virtualenvs/env1/bin/python3 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/ubuntu/.virtualenvs/env1/bin/python3 -m pip install --upgrade pip' command.


## Upload Datasets

In [2]:
cd /content/drive/My Drive/Repos/ExtractValues

[Errno 2] No such file or directory: '/content/drive/My Drive/Repos/ExtractValues'
/mnt/c/Users/Danie/Google Drive/repos/streamlit/NDFD


In [2]:
# Landslide 
landslide_shp = gpd.read_file('Flood_and_Landslide_Datasets/landslides_1_4326.shp')
landslide_json = 'Flood_and_Landslide_Datasets/landslides_1_4326.geojson'
#landslide_shp.head()

# Flood Risk (Vectorised)
flood_shp = gpd.read_file('Flood_and_Landslide_Datasets/geonode_flood_hazard_map_vector.shp')
flood_gj = geojson.load(open('Flood_and_Landslide_Datasets/geonode_flood_hazard_map_vector.geojson')) # Import geojson file # https://stackoverflow.com/questions/42753745/how-can-i-parse-geojson-with-python

print(flood_shp.head())

gj_features = flood_gj['features']
print(gj_features[0])

   FloodRisk                                           geometry
0          4  POLYGON ((-61.42133 15.63611, -61.42115 15.636...
1          4  POLYGON ((-61.42170 15.63574, -61.42152 15.635...
2          2  POLYGON ((-61.42175 15.63541, -61.42152 15.635...
3          4  POLYGON ((-61.42175 15.63430, -61.42156 15.634...
4          3  POLYGON ((-61.42193 15.63375, -61.42175 15.633...
{"geometry": {"coordinates": [[[[-61.421331, 15.636108], [-61.421146, 15.636108], [-61.421146, 15.635923], [-61.421331, 15.635923], [-61.421331, 15.636108]]]], "type": "MultiPolygon"}, "properties": {"Color": "#fdae61", "FloodRisk": 4}, "type": "Feature"}


## Define Point(s)

In [3]:
#===== Define Point(s) ================================
# Below are some points and expected results for checking

#x, y = (-61.37618,15.43130) # should return 2 & "NO Landslide"
#x, y = (-61.346482,15.393996) # should return 1 & "NO Landslide"

#x, y = (-61.346078,15.394703) # should return 1 & Pol_1
x, y = (-61.419855,15.396184) # should return 3 & Pol_1771
#x, y = (-61.415726,15.399853) # should return 1 & Pol_16
#x, y = (-61.413723,15.402079) # should return 5 & Pol_16

longitude=x; latitude=y

p = Point(x,y)
#======================================================

# Iteractive Plot with Folium


In [4]:
# Fill polygons in Folium *** https://stackoverflow.com/questions/35516318/plot-colored-polygons-with-geodataframe-in-folium ***
colors = ['#2b83ba', '#abdda4', '#ffffbf', '#fdae61', '#d7191c'] # these have been assigned to each FloodRisk category in the GeoJSON file on QGIS!!!
# Ideally here I would extract the unique color codes from the geojson file directly!!!

m = folium.Map(location=[latitude, longitude], zoom_start=11)

# Show Landslide GeoJSON to the map
folium.GeoJson(
    landslide_json,
    name='Landslide'
).add_to(m)

import branca
# Setup colormap MUST USE SAME COLORS AS QGIS GEOJSON FILE!!!!
levels = len(colors)
cmap = branca.colormap.LinearColormap(colors, vmin=1, vmax=5).to_step(levels-1)
cmap.add_to(m)

# folium.GeoJson(
#     flood_gj,
#     name='Flood Risk',
#     style_function=lambda feature: {
#         'fillColor': feature['properties']['Color'],
#         'color' : feature['properties']['Color'],
#         'weight' : 1,
#         'fillOpacity' : 0.3,
#         }
#     ).add_to(m)

# # add static marker 
# tooltip = "Selected Point"
# folium.Marker(
#     [latitude, longitude], tooltip=tooltip
# ).add_to(m)

# Enable lat-long Popup; LayerControl; Call to render Folium map in Streamlit
m.add_child(folium.ClickForMarker(popup='Waypoint (Double-click to remove it)')) # and click-for-marker functionality (dynamic)

m.add_child(folium.LatLngPopup()) # It's not possible to save lat long automatically from clicking on it :-( . # https://github.com/python-visualization/folium/issues/520

folium.LayerControl().add_to(m)

m


# Extract Values 

## Landslides Polygons

In [8]:
import geopandas
from shapely.geometry import *

p1 = Point(.5,.5)
p2 = Point(.5,1)
p3 = Point(3,1)

g = Polygon([(0,0), (0,2), (2,2), (2,0)])

def point_inside_shape(point, shape):
    #point of type Point
    #shape of type Polygon
    pnt = geopandas.GeoDataFrame(geometry=[point], index=['A'])
    return(pnt.within(shape).iloc[0])

for p in [p1, p2, p3]:
    print(point_inside_shape(p, g))

True
True
False


In [7]:
landslide_code = 'No Landslide'

# From a given Point coordinates, quickly/efficiently check if it's contained in any polygons geometry, and print out the LANDSLIDE code of that polygon if so. 
# this works, but is this teh most efficient way?!? Think it can be improved with lampda / apply / map, without iterating on the whole dataframe?
for elem in landslide_shp.loc[:,'geometry']:
  if p.within(elem): 
    landslide_code = landslide_shp.loc[landslide_shp.loc[:,'geometry'] == elem]['LANDSLIDES'].values[0]

print('The point is contained in the polygon:', landslide_code)

# or, in a nested one-line: 
#a = [print('The point is contained in the polygon:', f.loc[f.loc[:,'geometry'] == elem]['LANDSLIDES'].values[0]) for elem in f.loc[:,'geometry'] if p.within(elem)]

The point is contained in the polygon: Pol_1771


## Flood Risk Raster

In [ ]:
flood_shp.head()

FloodRisk                                           geometry
0          4  POLYGON ((-61.42133 15.63611, -61.42115 15.636...
1          4  POLYGON ((-61.42170 15.63574, -61.42152 15.635...
2          2  POLYGON ((-61.42175 15.63541, -61.42152 15.635...
3          4  POLYGON ((-61.42175 15.63430, -61.42156 15.634...
4          3  POLYGON ((-61.42193 15.63375, -61.42175 15.633...

In [ ]:
frisk_code = 'No Landslide'

# From a given Point coordinates, quickly/efficiently check if it's contained in any polygons geometry, and print out the LANDSLIDE code of that polygon if so. 
# this works, but is this teh most efficient way?!? Think it can be improved with lampda / apply / map, without iterating on the whole dataframe?
for elem in flood_shp.loc[:,'geometry']:
  if p.within(elem): 
    frisk_code = flood_shp.loc[flood_shp.loc[:,'geometry'] == elem]['FloodRisk'].values[0]

print('Flood risk category:', frisk_code)

Flood risk category: 3


# Both Together

In [ ]:
print(f'Selected coordinates: ({x}, {y})')
print('Landslide polygon:', landslide_code)
print('Flood risk category:', frisk_code)

Selected coordinates: (-61.419855, 15.396184)
Landslide polygon: Pol_1771
Flood risk category: 3
